In [1]:

import os
import copy
import time
import pickle
import numpy as np
import easydict
from tqdm import tqdm

import torch
from tensorboardX import SummaryWriter

from options import args_parser
from update import LocalUpdate, test_inference
from models import MLP, CNNMnist, CNNFashion_Mnist, CNNCifar, CNNCifar_fedVC, CNNCifar_VCBN, CNNCifar_VCGN, CNNCifar_WS
from utils import get_dataset, average_weights, exp_details, get_logger, CSVLogger
from fed_cifar100 import load_partition_data_federated_cifar100
from resnet_gn import resnet18
from resnet import ResNet32_test
from vgg import vgg11_bn, vgg11
import random
import logging
import datetime
from test import main_test


In [2]:
import matplotlib.pyplot as plt
%matplotlib inline
import matplotlib.style as style
style.use('seaborn')

import warnings
warnings.filterwarnings('ignore')

In [3]:
net_loss_list = []
net_acc_list = []
net_loss_itr_list = []
net_grad_conv_list = []
net_grad_fc_list = []
net_grad_norm_list = []

In [4]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.1,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 1
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)

INFO:root:{'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 0.1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\FedCifar100_frac0.01', 'exp_folder': 'FedCifar100_frac0.01', 'resume': None, 'lr_decay': 1}
03/08 11:33:52 AM | {'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 0.1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'ho

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
03/08 11:34:29 AM |  
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 4.357558526992798
03/08 11:34:29 AM | Training Loss : 4.357558526992798
INFO:root:Train Accuracy: 1.04% 

03/08 11:34:29 AM | Train Accuracy: 1.04% 

  0%|                                                                               | 1/4000 [00:03<3:48:10,  3.42s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
03/08 11:34:30 AM |  
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 4.574940528869629
03/08 11:34:30 AM | Training Loss : 4.574940528869629
INFO:root:Train Accuracy: 1.23% 

03/08 11:34:30 AM | Train Accuracy: 1.23% 

  0%|                                                                               | 2/4000 [00:04<2:23:32,  2.15s/it]INFO:root: 
Avg Training Stats after 3 global rounds:
0

INFO:root:Train Accuracy: 1.82% 

03/08 11:34:54 AM | Train Accuracy: 1.82% 

  0%|▍                                                                             | 20/4000 [00:28<1:27:54,  1.33s/it]INFO:root: 
Avg Training Stats after 21 global rounds:
03/08 11:34:55 AM |  
Avg Training Stats after 21 global rounds:
INFO:root:Training Loss : 4.028015098571777
03/08 11:34:55 AM | Training Loss : 4.028015098571777
INFO:root:Train Accuracy: 2.01% 

03/08 11:34:55 AM | Train Accuracy: 2.01% 

  1%|▍                                                                             | 21/4000 [00:29<1:27:50,  1.32s/it]INFO:root: 
Avg Training Stats after 22 global rounds:
03/08 11:34:56 AM |  
Avg Training Stats after 22 global rounds:
INFO:root:Training Loss : 4.2081893634796135
03/08 11:34:56 AM | Training Loss : 4.2081893634796135
INFO:root:Train Accuracy: 1.37% 

03/08 11:34:56 AM | Train Accuracy: 1.37% 

  1%|▍                                                                             | 22/40

INFO:root:Training Loss : 4.157078685760498
03/08 11:35:20 AM | Training Loss : 4.157078685760498
INFO:root:Train Accuracy: 2.26% 

03/08 11:35:20 AM | Train Accuracy: 2.26% 

  1%|▊                                                                             | 40/4000 [00:54<1:24:48,  1.29s/it]INFO:root: 
Avg Training Stats after 41 global rounds:
03/08 11:35:21 AM |  
Avg Training Stats after 41 global rounds:
INFO:root:Training Loss : 4.003678712844848
03/08 11:35:21 AM | Training Loss : 4.003678712844848
INFO:root:Train Accuracy: 1.85% 

03/08 11:35:21 AM | Train Accuracy: 1.85% 

  1%|▊                                                                             | 41/4000 [00:55<1:24:34,  1.28s/it]INFO:root: 
Avg Training Stats after 42 global rounds:
03/08 11:35:22 AM |  
Avg Training Stats after 42 global rounds:
INFO:root:Training Loss : 3.908744525909424
03/08 11:35:22 AM | Training Loss : 3.908744525909424
INFO:root:Train Accuracy: 2.30% 

03/08 11:35:22 AM | Train Accuracy: 2.

...

 99%|███████████████████████████████████████████████████████████████████████████▏| 3957/4000 [1:47:08<01:35,  2.22s/it]INFO:root: 
Avg Training Stats after 3958 global rounds:
03/08 01:21:36 PM |  
Avg Training Stats after 3958 global rounds:
INFO:root:Training Loss : 0.07666192691773176
03/08 01:21:36 PM | Training Loss : 0.07666192691773176
INFO:root:Train Accuracy: 31.20% 

03/08 01:21:36 PM | Train Accuracy: 31.20% 

 99%|███████████████████████████████████████████████████████████████████████████▏| 3958/4000 [1:47:10<01:33,  2.22s/it]INFO:root: 
Avg Training Stats after 3959 global rounds:
03/08 01:21:38 PM |  
Avg Training Stats after 3959 global rounds:
INFO:root:Training Loss : 0.11942307148128747
03/08 01:21:38 PM | Training Loss : 0.11942307148128747
INFO:root:Train Accuracy: 31.20% 

03/08 01:21:38 PM | Train Accuracy: 31.20% 

 99%|███████████████████████████████████████████████████████████████████████████▏| 3959/4000 [1:47:13<01:31,  2.24s/it]INFO:root: 
Avg Training Stats 

03/08 01:22:21 PM |  
Avg Training Stats after 3977 global rounds:
INFO:root:Training Loss : 0.0846423008525744
03/08 01:22:21 PM | Training Loss : 0.0846423008525744
INFO:root:Train Accuracy: 31.39% 

03/08 01:22:22 PM | Train Accuracy: 31.39% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3977/4000 [1:47:56<00:54,  2.35s/it]INFO:root: 
Avg Training Stats after 3978 global rounds:
03/08 01:22:24 PM |  
Avg Training Stats after 3978 global rounds:
INFO:root:Training Loss : 0.1506023938395083
03/08 01:22:24 PM | Training Loss : 0.1506023938395083
INFO:root:Train Accuracy: 31.96% 

03/08 01:22:24 PM | Train Accuracy: 31.96% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3978/4000 [1:47:58<00:51,  2.33s/it]INFO:root: 
Avg Training Stats after 3979 global rounds:
03/08 01:22:26 PM |  
Avg Training Stats after 3979 global rounds:
INFO:root:Training Loss : 0.12970902936533096
03/08 01:22:26 PM | Training Loss : 0.129

INFO:root:Train Accuracy: 32.58% 

03/08 01:23:03 PM | Train Accuracy: 32.58% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3996/4000 [1:48:37<00:08,  2.18s/it]INFO:root: 
Avg Training Stats after 3997 global rounds:
03/08 01:23:05 PM |  
Avg Training Stats after 3997 global rounds:
INFO:root:Training Loss : 0.03365646329708397
03/08 01:23:05 PM | Training Loss : 0.03365646329708397
INFO:root:Train Accuracy: 32.61% 

03/08 01:23:05 PM | Train Accuracy: 32.61% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3997/4000 [1:48:39<00:06,  2.18s/it]INFO:root: 
Avg Training Stats after 3998 global rounds:
03/08 01:23:07 PM |  
Avg Training Stats after 3998 global rounds:
INFO:root:Training Loss : 0.0809414101485163
03/08 01:23:07 PM | Training Loss : 0.0809414101485163
INFO:root:Train Accuracy: 32.31% 

03/08 01:23:07 PM | Train Accuracy: 32.31% 

100%|███████████████████████████████████████████████████████████████████

 Saving checkpoints to ../save/checkpoint\FedCifar100_frac0.01\cifar100_resnet18_T[4000]_C[0.01]_iid[2]_E[1]_B[20]...


INFO:root: 
 Results after 4000 global rounds of training:
03/08 01:23:13 PM |  
 Results after 4000 global rounds of training:
INFO:root:|---- Test Accuracy: 32.49%
03/08 01:23:13 PM | |---- Test Accuracy: 32.49%


In [5]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 1,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 1
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)

INFO:root:{'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\FedCifar100_frac0.01', 'exp_folder': 'FedCifar100_frac0.01', 'resume': None, 'lr_decay': 1}
03/08 01:25:50 PM | {'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_n

03/08 01:26:18 PM | ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
      (relu): ReLU(inplace=True)
      (bn2): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): Gr

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
03/08 01:26:27 PM |  
Avg Training Stats after 1 global rounds:
03/08 01:26:27 PM |  
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 329.5675806427002
03/08 01:26:27 PM | Training Loss : 329.5675806427002
03/08 01:26:27 PM | Training Loss : 329.5675806427002
INFO:root:Train Accuracy: 0.72% 

03/08 01:26:27 PM | Train Accuracy: 0.72% 

03/08 01:26:27 PM | Train Accuracy: 0.72% 

  0%|                                                                               | 1/4000 [00:01<1:37:26,  1.46s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
03/08 01:26:28 PM |  
Avg Training Stats after 2 global rounds:
03/08 01:26:28 PM |  
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 4.357372741699218
03/08 01:26:28 PM | Training Loss : 4.357372741699218
03/08 01:26:28 PM | Traini

03/08 01:26:46 PM |  
Avg Training Stats after 15 global rounds:
03/08 01:26:46 PM |  
Avg Training Stats after 15 global rounds:
INFO:root:Training Loss : 4.210204944610595
03/08 01:26:46 PM | Training Loss : 4.210204944610595
03/08 01:26:46 PM | Training Loss : 4.210204944610595
INFO:root:Train Accuracy: 1.22% 

03/08 01:26:46 PM | Train Accuracy: 1.22% 

03/08 01:26:46 PM | Train Accuracy: 1.22% 

  0%|▎                                                                             | 15/4000 [00:20<1:32:09,  1.39s/it]INFO:root: 
Avg Training Stats after 16 global rounds:
03/08 01:26:48 PM |  
Avg Training Stats after 16 global rounds:
03/08 01:26:48 PM |  
Avg Training Stats after 16 global rounds:
INFO:root:Training Loss : 4.469875583648682
03/08 01:26:48 PM | Training Loss : 4.469875583648682
03/08 01:26:48 PM | Training Loss : 4.469875583648682
INFO:root:Train Accuracy: 0.89% 

03/08 01:26:48 PM | Train Accuracy: 0.89% 

03/08 01:26:48 PM | Train Accuracy: 0.89% 

  0%|▎            

...

 99%|███████████████████████████████████████████████████████████████████████████▎| 3963/4000 [1:51:39<01:22,  2.23s/it]INFO:root: 
Avg Training Stats after 3964 global rounds:
03/08 03:18:07 PM |  
Avg Training Stats after 3964 global rounds:
03/08 03:18:07 PM |  
Avg Training Stats after 3964 global rounds:
INFO:root:Training Loss : 4.554343471527099
03/08 03:18:07 PM | Training Loss : 4.554343471527099
03/08 03:18:07 PM | Training Loss : 4.554343471527099
INFO:root:Train Accuracy: 0.59% 

03/08 03:18:07 PM | Train Accuracy: 0.59% 

03/08 03:18:07 PM | Train Accuracy: 0.59% 

 99%|███████████████████████████████████████████████████████████████████████████▎| 3964/4000 [1:51:41<01:19,  2.21s/it]INFO:root: 
Avg Training Stats after 3965 global rounds:
03/08 03:18:09 PM |  
Avg Training Stats after 3965 global rounds:
03/08 03:18:09 PM |  
Avg Training Stats after 3965 global rounds:
INFO:root:Training Loss : 4.320116672515869
03/08 03:18:09 PM | Training Loss : 4.320116672515869
03/08 03

 99%|███████████████████████████████████████████████████████████████████████████▌| 3977/4000 [1:52:10<00:50,  2.21s/it]INFO:root: 
Avg Training Stats after 3978 global rounds:
03/08 03:18:37 PM |  
Avg Training Stats after 3978 global rounds:
03/08 03:18:37 PM |  
Avg Training Stats after 3978 global rounds:
INFO:root:Training Loss : 4.53156078338623
03/08 03:18:37 PM | Training Loss : 4.53156078338623
03/08 03:18:37 PM | Training Loss : 4.53156078338623
INFO:root:Train Accuracy: 1.32% 

03/08 03:18:38 PM | Train Accuracy: 1.32% 

03/08 03:18:38 PM | Train Accuracy: 1.32% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3978/4000 [1:52:12<00:48,  2.20s/it]INFO:root: 
Avg Training Stats after 3979 global rounds:
03/08 03:18:39 PM |  
Avg Training Stats after 3979 global rounds:
03/08 03:18:39 PM |  
Avg Training Stats after 3979 global rounds:
INFO:root:Training Loss : 4.330639600753784
03/08 03:18:40 PM | Training Loss : 4.330639600753784
03/08 03:18

100%|███████████████████████████████████████████████████████████████████████████▊| 3991/4000 [1:52:41<00:19,  2.21s/it]INFO:root: 
Avg Training Stats after 3992 global rounds:
03/08 03:19:08 PM |  
Avg Training Stats after 3992 global rounds:
03/08 03:19:08 PM |  
Avg Training Stats after 3992 global rounds:
INFO:root:Training Loss : 4.385274658203125
03/08 03:19:08 PM | Training Loss : 4.385274658203125
03/08 03:19:08 PM | Training Loss : 4.385274658203125
INFO:root:Train Accuracy: 0.74% 

03/08 03:19:09 PM | Train Accuracy: 0.74% 

03/08 03:19:09 PM | Train Accuracy: 0.74% 

100%|███████████████████████████████████████████████████████████████████████████▊| 3992/4000 [1:52:43<00:17,  2.21s/it]INFO:root: 
Avg Training Stats after 3993 global rounds:
03/08 03:19:11 PM |  
Avg Training Stats after 3993 global rounds:
03/08 03:19:11 PM |  
Avg Training Stats after 3993 global rounds:
INFO:root:Training Loss : 4.533517074584961
03/08 03:19:11 PM | Training Loss : 4.533517074584961
03/08 03

 Saving checkpoints to ../save/checkpoint\FedCifar100_frac0.01\cifar100_resnet18_T[4000]_C[0.01]_iid[2]_E[1]_B[20]...


INFO:root: 
 Results after 4000 global rounds of training:
03/08 03:19:28 PM |  
 Results after 4000 global rounds of training:
03/08 03:19:28 PM |  
 Results after 4000 global rounds of training:
INFO:root:|---- Test Accuracy: 0.98%
03/08 03:19:28 PM | |---- Test Accuracy: 0.98%
03/08 03:19:28 PM | |---- Test Accuracy: 0.98%


In [19]:
print(net_loss_itr_list[0])

[[4.574864387512207, 4.48342227935791, 4.416894912719727, 4.040899753570557, 3.4769790172576904], [3.5251293182373047, 4.066310405731201, 3.6416027545928955, 2.820087432861328, 3.4659924507141113], [3.4627528190612793, 3.0241174697875977, 3.770826816558838, 2.614158868789673, 3.0087082386016846], [2.852628231048584, 3.429013729095459, 2.794403553009033, 3.208165407180786, 3.125577926635742], [3.2077510356903076, 3.0814690589904785, 2.677584171295166, 3.029737710952759, 2.4070920944213867], [3.6265621185302734, 3.2393202781677246, 2.9076995849609375, 2.6133856773376465, 2.8745875358581543], [3.0157415866851807, 3.671929121017456, 2.686880350112915, 3.0714216232299805, 2.0005440711975098], [3.242640256881714, 3.521132707595825, 3.1095919609069824, 2.9694581031799316, 2.6507327556610107], [2.9211533069610596, 2.860048770904541, 2.729557514190674, 3.48266863822937, 2.9689176082611084], [2.907616138458252, 3.2213146686553955, 2.1593899726867676, 2.4649345874786377, 2.7938919067382812], [2.5

In [14]:
args = easydict.EasyDict({
    "model": 'resnet18_ws',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'clip',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 1,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 0.9
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)

INFO:root:{'model': 'resnet18_ws', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'clip', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\FedCifar100_frac0.01', 'exp_folder': 'FedCifar100_frac0.01', 'resume': None, 'lr_decay': 0.9}
03/08 04:43:39 PM | {'model': 'resnet18_ws', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'clip', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.01, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0.9, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 10, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 

KeyboardInterrupt: 

In [ ]:
args = easydict.EasyDict({
    "model": 'resnet18_ws',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'clip',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 5,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 0.9
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)

In [ ]:
args = easydict.EasyDict({
    "model": 'resnet18_ws',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.1,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 1
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)

In [ ]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.01,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.01,
    'momentum': 0.9,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 10,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'FedCifar100_frac0.01',
    'resume': None,
    'lr_decay': 1
})

train_loss, val_acc_list, batch_loss_list, conv_grad_list, fc_grad_list, total_grad_list = main_test(args)
net_loss_list.append(train_loss)
net_acc_list.append(val_acc_list)
net_loss_itr_list.append(batch_loss_list)
net_grad_conv_list.append(conv_grad_list)
net_grad_fc_list.append(fc_grad_list)
net_grad_norm_list.append(total_grad_list)